### An example of BCH code that corrects up to 2 errors 

In [1]:
import os 
os.chdir('C:\\Users\\usuario\\ownCloud\\public_html\\CC2')
# Current extension patch to CC
from CC_x import *

def alternant_decoder(y,C):
    if not isinstance(y,list) and not isinstance(y,Vector_type):
        return 'AD error: wrong input type'
    K = K_(C)
    if K_(y) != K:
        if is_sub_domain(K,K_(y)):
            if isinstance(y,list): y = vector(K,y)
            if not isinstance(y,Vector_type):
                return "AD error: Argument is not a vector"
        else:
            return "AD error: Fields of argument and code incompatible"
    else: 
        if isinstance(y,list): y = vector(K,y)
        if not isinstance(y,Vector_type):
            return "AD error: Argument is not a vector"
    
    h = h_(C)
    if len(y) != len(h):
        return "AD error: Vector argument has wrong length"
    r = r_(C); a = a_(C); b = b_(C)
    H = H_(C); K1 = K_(H)
    y1 = pull(y,K)
    s = y1*H.transpose()
    
    if is_zero(s): 
        print("AD: Input is a code vector")
        return y1
    [_,z] = polynomial_ring(K1,'z','K[z]')
    S = polynomial(s,z)
    
    if degree(S)< r//2 or trailing_degree(S)>= r//2:
        return "AD: Non-decodable vector: extraneous syndrome"
        
    (L,E)=sugiyama(z**r,S,r//2)
    M = zero_positions(L,b)
    if len(M)< degree(L): return 'AD error: undecodable vector: too few roots'
    
    if K == Zn(2):
        for j in range(len(M)):
            y1[M[j]] += 1 
        show('Corrected positions:',M)
        return y1
    
    if len(M)<degree(L):
        return "AD error: non-decodable vector: too few locator roots"
    L = der(L)
    err = []
    for m in M:
        x = (a[m]*evaluate(E,b[m]))/(h[m]*evaluate(L,b[m]))
        x = pull(x,K)
        if not belongs(x,K):
            return "AD error: Non-decodable vector: Forney value not in base field"
        err += [-x]
        y1[m] = y1[m]+x
    if is_zero(y1*H.transpose()):
        print("AD: Successful decoding with error table:\n",M,'\n',vector(err))
        return y1
    else: return "AD error: output vector has non-zero syndrome"
# alias
BMS = AD = alternant_decoder

In [2]:
K = Zn(2)
[F,a] = extension(Zn(2), [1,0,0,1,1],'a','F') # F16

n = order(a)

C=BCH(a,5)

y = vector(K,[1,0,0,0,0,0,1,1,1,0,0,0,1,0,0])
show('y =',y)
x = BMS(y,C)

show(x,nl)

show(BMS(x,C),nl)

y = vector(K,[1,1,1,0,0,0,0,0,0,0,0,0,0,0,0])
show('y =',y)
x1 = BMS(y,C)
show(x1,nl)

show(BMS(x1,C))

# Since we have found a code vectors of weight 5, d_C = 5.

y = [1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 1, 0, 0]
Corrected positions: [4, 12]
[1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0] 

AD: Input is a code vector
[1, 0, 0, 0, 1, 0, 1, 1, 1, 0, 0, 0, 0, 0, 0] 

y = [1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
Corrected positions: [9, 13]
[1, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0] 

AD: Input is a code vector
[1, 1, 1, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0]
